# Data exploration
This notebook provides an example how the data has been loaded and accessed for further analysis.

## Setup notebook

In [1]:
# Enable autoreloading of our modules. 
# Most of the code will be located in the /src/ folder, 
# and then called from the notebook.
%matplotlib inline
%reload_ext autoreload
%autoreload

In [2]:
from IPython.core.debugger import set_trace

import pandas as pd
import numpy as np
import os

import plotly
import plotly.graph_objs as go
import plotly.plotly as py
import plotly.tools as tls
import plotly.figure_factory as ff
import plotly.io as pio


import matplotlib
from matplotlib import cm
import colorlover as cl

from ipywidgets import widgets, Output
from IPython.display import display, clear_output, Image, HTML

from sklearn.metrics import confusion_matrix

## Import data
Import our data into pandas Dataframes for the analysis. Data files are `.csv` files which are stored in the `./data/interim/` folder.

In [3]:
def df_from_csv(csv, index_col, data_folder='../data/interim'):
    print('Importing {}'.format(csv))
    return pd.read_csv(os.path.join(data_folder,csv), index_col=index_col)

df_waves = df_from_csv('waves.csv', index_col=[0, 1])
df_tides = df_from_csv('tides.csv', index_col=[0, 1])
df_profiles = df_from_csv('profiles.csv', index_col=[0, 1, 2])
df_sites = df_from_csv('sites.csv', index_col=[0])
df_profile_features = df_from_csv('profile_features.csv', index_col=[0])

# Note that the forecasted data sets should be in the same order for impacts and twls
impacts = {
    'forecasted': {
        'foreshore_slope_sto06': df_from_csv('impacts_forecasted_foreshore_slope_sto06.csv', index_col=[0]),
        'mean_slope_sto06': df_from_csv('impacts_forecasted_mean_slope_sto06.csv', index_col=[0]),
        },
    'observed': df_from_csv('impacts_observed.csv', index_col=[0])
    }


twls = {
    'forecasted': {
        'foreshore_slope_sto06': df_from_csv('twl_foreshore_slope_sto06.csv', index_col=[0, 1]),
        'mean_slope_sto06':df_from_csv('twl_mean_slope_sto06.csv', index_col=[0, 1]),
    }
}
print('Done!')

Importing waves.csv
Importing tides.csv
Importing profiles.csv


C:\Users\z5189959\Desktop\nsw-2016-storm-impact\.venv\lib\site-packages\numpy\lib\arraysetops.py:522: FutureWarning:

elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison



Importing sites.csv
Importing profile_features.csv
Importing impacts_forecasted_foreshore_slope_sto06.csv
Importing impacts_forecasted_mean_slope_sto06.csv
Importing impacts_observed.csv
Importing twl_foreshore_slope_sto06.csv
Importing twl_mean_slope_sto06.csv
Done!


## Profile/timeseries dashboard

The following interactive data explorer displays information on a per `site_id` basis. It can be used to examine pre/post storm cross-sections, water level time series and observed/predicted storm impacts.

In [4]:
# Create widgets for filtering by observed and forecasted impacts
filter_title = widgets.HTML(
    value="<b>Filter by observed and predicted impacts:</b>", )

titles = ['Observed Impacts']
selectboxes = [
    widgets.SelectMultiple(
        options=impacts['observed'].storm_regime.dropna().unique().tolist(),
        value=impacts['observed'].storm_regime.dropna().unique().tolist(),
        disabled=False)
]

# Iterate through each of our forecasted impacts
for forecast in impacts['forecasted']:
    selectboxes.append(
        widgets.SelectMultiple(
            options=impacts['forecasted'][forecast].storm_regime.dropna().
            unique().tolist(),
            value=impacts['forecasted'][forecast].storm_regime.dropna().
            unique().tolist(),
            disabled=False))
    titles.append('Forecasted: {}'.format(forecast))

titles = [widgets.HTML(value=title) for title in titles]

children = widgets.HBox(children=[
    widgets.VBox(children=[title, box])
    for title, box in zip(titles, selectboxes)
])
filter_container = widgets.VBox(children=[filter_title, children])

# Create widgets for selecting site_id
site_id_title = widgets.HTML(value="<b>Filter by site_id:</b>", )

site_id_select = widgets.Dropdown(
    description='site_id:   ',
    value='NARRA0001',
        options=df_profiles.index.get_level_values('site_id').unique().
        sort_values().tolist(),
#     options=df_no_crests.index.tolist(),
)

site_id_impacts = widgets.HTML(value="", )

site_id_container = widgets.HBox(children=[
    widgets.VBox(
        children=[site_id_title,
                  widgets.HBox(children=[site_id_select])]), site_id_impacts
])

# Build colors for each of our forecasts
colors = list(
    reversed(cl.scales[str(max(len(impacts['forecasted']),
                               3))]['seq']['YlGnBu']))

# Add panel for pre/post storm profiles
trace1 = go.Scatter(
    x=[0],
    y=[0],
    name='Pre Storm Profile',
    line=dict(color=('rgb(51,160,44)'), width=2))
trace2 = go.Scatter(
    x=[0],
    y=[0],
    name='Post Storm Profile',
    line=dict(color=('rgb(255,127,0)'), width=2))
trace3 = go.Scatter(
    x=[0],
    y=[0],
    name='Pre-storm dune crest',
    mode='markers',
    marker=dict(
        color='rgba(255,255,255,0)',
        size=10,
        line=dict(color='rgba(106,61,154, 1)', width=2)),
)
trace4 = go.Scatter(
    x=[0],
    y=[0],
    name='Pre-storm dune toe',
    mode='markers',
    marker=dict(
        color='rgba(255,255,255,0)',
        size=10,
        line=dict(color='rgba(202,178,214,1)', width=2)),
)

trace5 = go.Scatter(
    x=[0],
    y=[0],
    name='Post-storm dune crest',
    mode='markers',
    marker=dict(
        color='rgba(255,255,255,0)',
        size=10,
        line=dict(color='rgba(106,61,154, 1)', width=2),
        symbol='square'),
)
trace6 = go.Scatter(
    x=[0],
    y=[0],
    name='Post-storm dune toe',
    mode='markers',
    marker=dict(
        color='rgba(255,255,255,0)',
        size=10,
        line=dict(color='rgba(202,178,214,1)', width=2),
        symbol='square'),
)

forecast_traces = []
for forecast, color in zip(impacts['forecasted'], colors):
    forecast_traces.append(
        go.Scatter(
            x=[0],
            y=[0],
            name='Peak R_high: {}'.format(forecast),
            mode='lines',
            line=dict(
                color=color,
                width=4,
            )))

layout = go.Layout(
    title='Bed Profiles',
    height=300,
    legend=dict(font={'size': 10}),
    margin=dict(t=50, b=50, l=50, r=20),
    xaxis=dict(
        title='x (m)',
        autorange=True,
        showgrid=True,
        zeroline=True,
        showline=True,
        range=[0, 200]),
    yaxis=dict(
        title='z (m)',
        autorange=False,
        showgrid=True,
        zeroline=True,
        showline=True,
        range=[-1, 20]))

g_profiles = go.FigureWidget(
    data=[trace1, trace2, trace3, trace4, trace5, trace6] + forecast_traces,
    layout=layout)

# Add panel for google maps
mapbox_access_token = 'pk.eyJ1IjoiY2hyaXNsZWFtYW4iLCJhIjoiY2pvNTY1MzZpMDc2OTN2bmw5MGsycHp5bCJ9.U2dwFg2c7RFjUNSayERUiw'

data = [
    go.Scattermapbox(
        lat=df_sites['lat'],
        lon=df_sites['lon'],
        mode='markers',
        marker=dict(size=10),
        text=df_sites.index.get_level_values('site_id'),
    ),
    go.Scattermapbox(
        lat=[0],
        lon=[0],
        mode='markers',
        marker=dict(
            size=20,
            color='rgb(255, 0, 0)',
            opacity=0.5,
        ),
        text=df_sites.index.get_level_values('site_id'),
    ),
]

layout = go.Layout(
    autosize=True,
    height=300,
    hovermode='closest',
    showlegend=False,
    margin=dict(t=50, b=50, l=20, r=20),
    mapbox=dict(
        accesstoken=mapbox_access_token,
        bearing=0,
        center=dict(lat=-33.7, lon=151.3),
        pitch=0,
        zoom=12,
        style='satellite-streets'),
)

fig = dict(data=data, layout=layout)
g_map = go.FigureWidget(data=data, layout=layout)

subplot = tls.make_subplots(3, 1, print_grid=False, shared_xaxes=True)
g_timeseries = go.FigureWidget(subplot)

# Add trace for Hs0
g_timeseries.add_trace(
    go.Scatter(
        x=[0, 1],
        y=[0, 1],
        name='Hs0',
    ),
    row=3,
    col=1,
)

# Add trace for Tp
g_timeseries.add_trace(
    go.Scatter(
        x=[0, 1],
        y=[0, 1],
        name='Tp',
    ),
    row=3,
    col=1,
)

# Add water levels
g_timeseries.add_trace(
    go.Scatter(
        x=[0, 3],
        y=[0, 3],
        name='Dune Crest',
        mode='lines',
        line=dict(color=('rgb(214, 117, 14)'), width=2, dash='dot')),
    row=1,
    col=1)

g_timeseries.add_trace(
    go.Scatter(
        x=[0, 3],
        y=[0, 3],
        name='Dune Toe',
        mode='lines',
        line=dict(color=('rgb(142, 77, 8)'), width=2, dash='dash')),
    row=1,
    col=1)

g_timeseries.add_trace(
    go.Scatter(
        x=[0, 3],
        y=[0, 3],
        name='Tide+Surge WL',
        line=dict(color=('rgb(8,51,137)'), width=2, dash='dot')),
    row=1,
    col=1)

for forecast, color in zip(twls['forecasted'], colors):
    g_timeseries.add_trace(
        go.Scatter(
            x=[0],
            y=[0],
            name='R_high: {}'.format(forecast),
            line=dict(color=color, width=3)),
        row=1,
        col=1)

# Add trace for each forecasted beta term
for forecast, color in zip(impacts['forecasted'], colors):
    g_timeseries.add_trace(
        go.Scatter(
            x=[0, 1],
            y=[0, 1],
            name='Beta: {}'.format(forecast),
            line=dict(color=color, width=3)),
        row=2,
        col=1,
    )

# Create axis for Tp on same plot as Hs
g_timeseries['layout']['yaxis4'] = {'overlaying': 'y3', 'side': 'right'}
g_timeseries.data[1]['yaxis'] = 'y4'

# Add labels to each axis
g_timeseries.layout['xaxis']['title'] = 'datetime'
g_timeseries.layout['yaxis1']['title'] = 'z (mAHD)'
g_timeseries.layout['yaxis2']['title'] = 'beta (-)'
g_timeseries.layout['yaxis3']['title'] = 'Hs0 (m)'
g_timeseries.layout['yaxis4']['title'] = 'Tp (s)'

# Update figure size
g_timeseries['layout'].update(height=400, legend=dict(font={'size': 10}))
g_timeseries['layout'].update(margin=dict(t=20, l=50, r=20, b=100))

# Add panel for some tables
titles = ['observed'] + [forecast for forecast in impacts['forecasted']]
titles = [widgets.HTML(value="{}".format(title)) for title in titles]


def get_observed_impacts_table(site_id):
    display(impacts['observed'].query("site_id=='{}'".format(site_id)).T)


def get_forecasted_impacts_table(site_id, forecast):
    display(impacts['forecasted'][forecast].query(
        "site_id=='{}'".format(site_id)).T)


impacts_table_observed = widgets.interactive_output(
    get_observed_impacts_table, {'site_id': site_id_select})
forecasted_impacts_tables = []
for forecast, title in zip(impacts['forecasted'], titles[1:]):
    forecasted_impacts_tables.append(
        widgets.interactive_output(get_forecasted_impacts_table, {
            'site_id': site_id_select,
            'forecast': title
        }))

tables = [impacts_table_observed] + forecasted_impacts_tables

title_tables = [
    widgets.VBox(children=[title, table])
    for title, table in zip(titles, tables)
]

tables_container = widgets.HBox(children=[*title_tables])


def update_profile(change):

    site_id = site_id_select.value

    if site_id is None:
        return

    site_profile = df_profiles.query('site_id == "{}"'.format(site_id))
    prestorm_profile = site_profile.query('profile_type == "prestorm"')
    poststorm_profile = site_profile.query('profile_type == "poststorm"')

    poststorm_x = poststorm_profile.index.get_level_values('x').tolist()
    poststorm_z = poststorm_profile.z.tolist()

    prestorm_x = prestorm_profile.index.get_level_values('x').tolist()
    prestorm_z = prestorm_profile.z.tolist()

    prestorm_site_features = df_profile_features.query(
        'site_id == "{}" and profile_type=="prestorm"'.format(site_id))
    prestorm_dune_crest_x = prestorm_site_features.dune_crest_x
    prestorm_dune_crest_z = prestorm_site_features.dune_crest_z
    prestorm_dune_toe_x = prestorm_site_features.dune_toe_x
    prestorm_dune_toe_z = prestorm_site_features.dune_toe_z

    poststorm_site_features = df_profile_features.query(
        'site_id == "{}" and profile_type=="poststorm"'.format(site_id))
    poststorm_dune_crest_x = poststorm_site_features.dune_crest_x
    poststorm_dune_crest_z = poststorm_site_features.dune_crest_z
    poststorm_dune_toe_x = poststorm_site_features.dune_toe_x
    poststorm_dune_toe_z = poststorm_site_features.dune_toe_z

    # Update beach profile section plots
    with g_profiles.batch_update():
        g_profiles.data[0].x = prestorm_x
        g_profiles.data[0].y = prestorm_z
        g_profiles.data[1].x = poststorm_x
        g_profiles.data[1].y = poststorm_z
        g_profiles.data[2].x = prestorm_dune_crest_x
        g_profiles.data[2].y = prestorm_dune_crest_z
        g_profiles.data[3].x = prestorm_dune_toe_x
        g_profiles.data[3].y = prestorm_dune_toe_z
        g_profiles.data[4].x = poststorm_dune_crest_x
        g_profiles.data[4].y = poststorm_dune_crest_z
        g_profiles.data[5].x = poststorm_dune_toe_x
        g_profiles.data[5].y = poststorm_dune_toe_z

        for n, forecast in enumerate(impacts['forecasted']):
            R_high = max(impacts['forecasted'][forecast].query(
                "site_id=='{}'".format(site_id)).R_high)
            g_profiles.data[6 + n].x = [200, 400]
            g_profiles.data[6 + n].y = [R_high, R_high]

    # Relocate plan of satellite imagery
    site_coords = df_sites.query('site_id == "{}"'.format(site_id))
    with g_map.batch_update():
        g_map.layout.mapbox['center'] = {
            'lat': site_coords['lat'].values[0],
            'lon': site_coords['lon'].values[0]
        }
        g_map.layout.mapbox['zoom'] = 15
        g_map.data[1].lat = [site_coords['lat'].values[0]]
        g_map.data[1].lon = [site_coords['lon'].values[0]]
        g_map.data[1].text = site_coords['lon'].index.get_level_values(
            'site_id').tolist()

    # Update time series plots
    df_waves_site = df_waves.query("site_id=='{}'".format(site_id))
    times = df_waves_site.index.get_level_values('datetime').tolist()
    Hs0s = df_waves_site.Hs0.tolist()
    Tps = df_waves_site.Tp.tolist()

    df_tide_site = df_tides.query("site_id=='{}'".format(site_id))
    mask = (df_tide_site.index.get_level_values('datetime') >= min(times)) & (
        df_tide_site.index.get_level_values('datetime') <= max(times))
    df_tide_site = df_tide_site.loc[mask]

    with g_timeseries.batch_update():
        g_timeseries.data[0].x = times
        g_timeseries.data[0].y = Hs0s
        g_timeseries.data[1].x = times
        g_timeseries.data[1].y = Tps

        # Update beta values
        idx_betas = [
            n for n, x in enumerate(g_timeseries.data) if 'Beta' in x.name
        ]
        for i, forecast in zip(idx_betas, twls['forecasted']):
            df_twl = twls['forecasted'][forecast].query(
                "site_id=='{}'".format(site_id))
            times = df_twl.index.get_level_values('datetime').tolist()
            beta = df_twl.beta.tolist()
            g_timeseries.data[i].x = times
            g_timeseries.data[i].y = beta

        g_timeseries.data[2].x = [min(times), max(times)]
        g_timeseries.data[3].x = [min(times), max(times)]
        g_timeseries.data[4].x = df_tide_site.index.get_level_values(
            'datetime')
        g_timeseries.data[2].y = prestorm_dune_crest_z.tolist(
        )[0], prestorm_dune_crest_z.tolist()[0],
        g_timeseries.data[3].y = prestorm_dune_toe_z.tolist(
        )[0], prestorm_dune_toe_z.tolist()[0],
        g_timeseries.data[4].y = df_tide_site.tide.tolist()

        # Update rhigh values
        idx_betas = [
            n for n, x in enumerate(g_timeseries.data) if 'R_high' in x.name
        ]
        for i, forecast in zip(idx_betas, twls['forecasted']):
            df_twl = twls['forecasted'][forecast].query(
                "site_id=='{}'".format(site_id))
            times = df_twl.index.get_level_values('datetime').tolist()
            R_high = df_twl.R_high.tolist()
            g_timeseries.data[i].x = times
            g_timeseries.data[i].y = R_high

    # Update site id impacts
    observed_regime = impacts['observed'].query(
        "site_id=='{}'".format(site_id)).storm_regime.values[0]
    site_id_impacts.value = "Observed: <b>{}</b><br>".format(observed_regime)

    for forecast in impacts['forecasted']:
        regime = impacts['forecasted'][forecast].query(
            "site_id=='{}'".format(site_id)).storm_regime.values[0]
        site_id_impacts.value += '{}: <b>{}</b><br>'.format(forecast, regime)


site_id_select.observe(update_profile, names="value")


def update_filter(change):

    # Iterate through each box, only keeping site_ids which are not filtered out by each box
    valid_site_ids = impacts['observed'].index.tolist()
    dfs = [impacts['observed']
           ] + [impacts['forecasted'][key] for key in impacts['forecasted']]

    for box, df in zip(selectboxes, dfs):
        valid_site_ids = list(
            set(valid_site_ids).intersection(
                set(df[df.storm_regime.isin(box.value)].index.tolist())))
    site_id_select.options = sorted(valid_site_ids)

    # TODO Update options in selectboxes with number of observations?


# Update the filter if any of the boxes changes
for box in selectboxes:
    box.observe(update_filter, names="value")

# Display our widgets!
widgets.VBox([
    filter_container, site_id_container,
    widgets.HBox([g_profiles, g_map]), g_timeseries, tables_container
])

In [85]:
for x in df_profiles.index.get_level_values('site_id').unique().sort_values().tolist():
    print(x)

AVOCAn0001
AVOCAn0002
AVOCAn0003
AVOCAn0004
AVOCAn0005
AVOCAn0006
AVOCAn0007
AVOCAn0008
AVOCAn0009
AVOCAs0001
AVOCAs0002
AVOCAs0003
AVOCAs0004
AVOCAs0005
AVOCAs0006
AVOCAs0007
AVOCAs0008
BILG0001
BILG0002
BILG0003
BILG0004
BILG0005
BLUEYS0001
BLUEYS0002
BLUEYS0003
BLUEYS0004
BLUEYS0005
BLUEYS0006
BOAT0001
BOAT0002
BOAT0003
BOAT0004
BOAT0005
BOOM0001
BOOM0002
BOOM0003
BOOM0004
BOOM0005
BOOM0006
BOOM0007
BOOM0008
BOOM0009
BOOM0010
BOOM0011
BOOM0012
BOOM0013
BOOM0014
CATHIE0001
CATHIE0002
CATHIE0003
CATHIE0004
CATHIE0005
CATHIE0006
CATHIE0007
CATHIE0008
CATHIE0009
CATHIE0010
CATHIE0011
CATHIE0012
CATHIE0013
CATHIE0014
CATHIE0015
CATHIE0016
CATHIE0017
CATHIE0018
CATHIE0019
CATHIE0020
CATHIE0021
CATHIE0022
CATHIE0023
CATHIE0024
CATHIE0025
CATHIE0026
CATHIE0027
CATHIE0028
CATHIE0029
CRESn0001
CRESn0002
CRESn0003
CRESn0004
CRESn0005
CRESn0006
CRESn0007
CRESn0008
CRESn0009
CRESn0010
CRESn0011
CRESn0012
CRESn0013
CRESn0014
CRESn0015
CRESn0016
CRESn0017
CRESn0018
CRESn0019
CRESn0020
CRESn0021
CR

## Confusion matrix
This visualization looks at how well the storm impact predictions performed. 

In [ ]:
# Create colorscale
rdylgr_cmap = matplotlib.cm.get_cmap('RdYlGn')

norm = matplotlib.colors.Normalize(vmin=0, vmax=255)

def matplotlib_to_plotly(cmap, pl_entries):
    h = 1.0/(pl_entries-1)
    pl_colorscale = []

    for k in range(pl_entries):
        C = list(map(np.uint8, np.array(cmap(k*h)[:3])*255))
        pl_colorscale.append([k*h, 'rgb'+str((C[0], C[1], C[2]))])

    return pl_colorscale

rdylgr = matplotlib_to_plotly(rdylgr_cmap, 255)



# Create widget for list of beaches.
beaches = df_sites.beach.unique().tolist()

beach_title = widgets.HTML(value="<b>Filter by beach:</b>", )

beach_select = widgets.SelectMultiple(
    options=beaches, value=beaches, disabled=False)

beach_container = widgets.VBox([beach_title, beach_select])

# Create confusion matrix for each forecasted impact data set
heatmaps = []
for forecast in impacts['forecasted']:

    z = [[.1, .3, .5, 2], [1.0, .8, .6, 1], [1.4, .28, 1.6, .21],
         [.6, .4, .2, 3]]

    x = ['swash', 'collision', 'overwash', 'inundation']
    y = list(reversed(x))

    z_text = z

    fig = ff.create_annotated_heatmap(z, x=x, y=y, annotation_text=z_text, colorscale=rdylgr)
    heatmap = go.FigureWidget(data=fig.data, layout=fig.layout)

    heatmap.layout.update(
        height=300, margin=go.layout.Margin(l=100, r=100, b=40, t=40, pad=0))
    heatmap.layout.xaxis.update(title='Predicted')
    heatmap.layout.yaxis.update(title='Observed')
    heatmap_title = widgets.HTML(value="<b>{}</b>".format(forecast) )
    heatmaps.append(widgets.VBox([heatmap_title, heatmap]))

    
def update_heatmaps(change):
    
    for forecast, heatmap in zip(impacts['forecasted'], heatmaps):
        selected_site_ids = df_sites[df_sites.beach.isin(beach_select.value)].index.tolist()

        df_ob = impacts['observed']
        df_fo = impacts['forecasted'][forecast]

        observed_regimes = df_ob[df_ob.index.isin(selected_site_ids)].storm_regime.dropna().rename("observed_regime")
        forecasted_regimes = df_fo[df_fo.index.isin(selected_site_ids)].storm_regime.dropna().rename("forecasted_regime")

        if any([observed_regimes.empty, forecasted_regimes.empty]):
            return
        
        df_compare = pd.concat([observed_regimes, forecasted_regimes], axis='columns', names=['a','b'], sort=True)
        df_compare.dropna(axis='index',inplace=True)

        z = confusion_matrix(df_compare.observed_regime.tolist(), df_compare.forecasted_regime.tolist(), labels = ['swash','collision','overwash','inundation'])
        z = np.flip(z,axis=0)
        z_list = list(reversed(z.tolist()))
        
        # Make incorrect values negative, so they get assigned a different color.
        # Better for visualization
        z_neg_incorrect = np.flip(np.identity(4),axis=0)
        z_neg_incorrect[z_neg_incorrect==0]= -1
        z_neg_incorrect = (z * z_neg_incorrect).tolist()
        
        # Also want to display percentages
        z_with_pct = []
        for row in z:
            new_row = []
            for val in row:
                new_row.append('{}<br>({}%)'.format(val, np.around(val/np.sum(z)*100,1)))
            z_with_pct.append(new_row)
        
        fig = ff.create_annotated_heatmap(z_neg_incorrect, x=x, y=y, annotation_text=z_with_pct)
        heatmap.children[1].data[0].z = z_neg_incorrect
        heatmap.children[1].layout.annotations = fig.layout.annotations

# Hook changes to beach filter to update confusion heatmaps
beach_select.observe(update_heatmaps, names="value")

# Display our widgets
widgets.VBox([beach_container, widgets.VBox(heatmaps)])



In [ ]:
# To output to file
# fig = heatmaps[1].children[1]
# img_bytes = pio.write_image(fig, 'fig1.png',format='png', width=600, height=400, scale=5)

# fig = g_profiles
# img_bytes = pio.write_image(fig, 'fig1.png',format='png', width=600, height=200, scale=5)


## Identify sites with no results

### Check forecast TWL
Most probable explanation for TWL's which are NaN'ed is that the prestorm dune toe are not defined.

In [57]:
df_twls = twls['forecasted']['mean_slope_sto06']

slope_mask = df_twls.groupby('site_id').agg({'beta': lambda x: x.isnull().sum() == len(x)}).beta
print('The following sites have no slope defined in the twl csv file:')
print(slope_mask.index[slope_mask].tolist())
print()

R_high_mask = df_twls.groupby('site_id').agg({'R_high': lambda x: x.isnull().sum() == len(x)}).R_high
print('The following sites have no R_high defined in the twl csv file:')
print(slope_mask.index[slope_mask].tolist())


The following sites have no slope defined in the twl csv file:
['ENTRA0078', 'ENTRA0079', 'MANNING0109']

The following sites have no R_high defined in the twl csv file:
['ENTRA0078', 'ENTRA0079', 'MANNING0109']


### Check observed impacts
Find sites which have no observed impacts. If we do not identify an observed storm regime, the site cannot be included when we're trying to compare predicted and observed impacts.

In [58]:
df_impacts = impacts['observed']
df_no_obs_impacts = df_impacts[df_impacts.storm_regime.isnull()]
no_obs_impacts_sites = df_no_obs_impacts.index

df_no_obs_impacts


prestorm_swash_vol  poststorm_swash_vol  swash_vol_change  \
site_id                                                                   
AVOCAn0009                4.5783               0.1110            4.4673   
AVOCAs0001                   NaN                  NaN               NaN   
AVOCAs0002               97.9463              26.6638           71.2825   
AVOCAs0003               70.7306              40.2020           30.7232   
AVOCAs0004               98.2859              45.4986           52.6330   
AVOCAs0005               95.5841              54.9753           40.5733   
AVOCAs0006              113.0441              67.8912           45.2582   
AVOCAs0007               65.3283              44.2821           21.4544   
AVOCAs0008               52.3933              45.2243            7.1728   
BILG0001                 20.3405               7.6207           12.7198   
BILG0002                156.4205              98.1716           58.1659   
BOAT0001                 23.8361              23.6865           -0.0926   
BOAT0002                 38.8398              14.0819           24.7579   
BOAT0003                 73.6809              17.8545           55.8264   
BOAT0004                 73.1954              23.1583           50.0372   
BOAT0005                 53.5122              22.4537           31.0585   
BOOM0001                236.4540             218.4918           20.8725   
CATHIE0024               63.6452              38.4261           25.2191   
CATHIE0026               75.1334              43.7179           31.0940   
CRESn0069                37.5896               8.3495           29.2401   
DEEWHYn0008                  NaN                  NaN               NaN   
DEEWHYn0009                  NaN                  NaN               NaN   
DEEWHYs0005              62.3514              24.9797           37.3716   
DEEWHYs0008               1.0688               1.3640            0.0000   
DIAMONDn0023             67.9416              21.1812           46.7603   
DIAMONDs0006             74.9357              42.4382           32.2536   
DIAMONDs0007            153.7639             127.9469           26.1595   
DUNBn0031                36.5301               6.3289           30.2012   
DUNBn0055               189.5283             134.2760           56.7139   
ELIZA0002                    NaN                  NaN               NaN   
...                          ...                  ...               ...   
STOCNs0170              198.2785             216.6368          -18.6067   
STOCNs0175              136.2126             114.1715           22.4984   
STOCNs0179               67.7795              45.3981           22.3815   
STOCNs0180              166.0813             149.5195           15.3441   
STOCNs0181               90.1147              98.9808           -9.1107   
STOCNs0182               67.8622              86.0118          -18.1671   
STOCNs0183              125.9085             137.7342          -12.6233   
STOCNs0184              146.6586             123.5371           23.2603   
STOCNs0185              141.5421             142.7279           -1.2619   
STOCNs0186              115.9148             123.1507           -7.8392   
STOCNs0187              126.5519             147.4371          -22.4452   
STOCNs0188              345.5234             353.8766          -11.3322   
STOCNs0189              171.6354             134.9192           35.8697   
STOCNs0190              151.4113             116.6381           35.0161   
STOCS0014                98.4991              57.3495           40.9006   
STOCS0043                36.4256              11.7208           24.7048   
WAMBE0005                    NaN                  NaN               NaN   
WAMBE0015                56.2724              16.0428           40.2296   
WAMBE0016                97.8849              39.8432           58.0417   
WAMBE0017                36.5683               8.5380           28.0303   
WAMBE0018                42.1423       

It looks like the problem comes from if we cannot identify the prestorm and post storm swash and berm volume changes.

### Check pre and post storm profiles
It looks like, for some reason, there are no post storm profiles (`STUART0011`) for some of the profiles. Not sure if this is a processing error, or it hasn't been included in the dataset.

### Check prestorm dune crests
If there are no prestorm dune crests defined, we cannot define a mean slope and hence we won't be able to get observed impacts

In [74]:
df_no_crests = df_profile_features.query('profile_type=="prestorm" & (dune_crest_x != dune_crest_x)')
print('{} sites have no dune crests:'.format(len(df_no_crests)))

for site_id in df_no_crests.index.tolist():
    print(site_id)

231 sites have no dune crests:
AVOCAn0009
AVOCAs0001
AVOCAs0002
AVOCAs0003
AVOCAs0004
AVOCAs0005
AVOCAs0006
AVOCAs0007
AVOCAs0008
BILG0001
BILG0002
BOAT0001
BOAT0002
BOAT0003
BOAT0004
BOAT0005
BOOM0001
CATHIE0026
CRESn0069
DEEWHYn0008
DEEWHYn0009
DEEWHYs0005
DEEWHYs0008
DIAMONDs0006
DIAMONDs0007
ENTRA0005
ENTRA0006
ENTRA0077
ENTRA0078
ENTRA0079
FOST0003
GRANTSn0004
GRANTSn0005
GRANTSn0006
GRANTSn0007
GRANTSn0008
GRANTSn0009
GRANTSn0021
GRANTSs0014
HARGs0003
HARGs0004
HARGs0005
HARR0056
LHOUSE0001
LHOUSE0002
LHOUSE0003
LHOUSE0004
LHOUSE0012
LHOUSE0013
LHOUSEs0015
MACM0008
MACM0012
MACM0013
MACM0014
MACM0015
MACM0016
MANNING0001
MANNING0002
MANNING0003
MANNING0004
MANNING0005
MANNING0101
MANNING0102
MANNING0103
MANNING0104
MANNING0105
MANNING0106
MANNING0107
MANNING0108
MANNING0109
MONA0001
MONA0002
MONA0003
MONA0014
MONA0015
MONA0016
MONA0017
MONA0018
MONA0019
MONA0020
MONA0021
NAMB0027
NAMB0041
NARRA0001
NARRA0028
NARRA0035
NINEMn0050
OLDBAR0035
PEARLn0001
PEARLn0002
PEARLn0003
PEARLn0